# Modeling with Scikit-Learn Regressor
- The support vector machine (SVM) is a data-classification algorithm that assigns new data elements to one of the labeled categories, it assumes that the data in question contains some possible target values. In Machine Learning or Data Science are quite familiar with the term Support Vector Machine, but Support Vector Regression (SVR) is a bit different from SVM. As the name suggests the SVR is a regression algorithm, so we can use SVR for working with continuous Values instead of Classification which is SVM. The basic idea of SVR is to find a function f(y) that has most ε deviation from the actually obtained target for the training data yi, and at the same time is as flat as possible. In other words, **we do not care about the errors as long as they are less than ε**. **This property determines the SVR to be less sensitive to outliers than the quadratic loss function.**

## 1. Preprocessing
- Lable-Encoding
- Log nomalization
- Standard scaling

# 2. Regressors : Scikit-Learn
- DecisionTree Regressor
- RandomForest Regressor
- Support Vector Regressor
- XGB Regressor
- Cross-validation and Results

# 3. Testing

In [1]:
%matplotlib inline
pd.options.mode.chained_assignment = None
pd.set_option('display.max_columns', 500)
pd.set_option('display.max_rows', 500)
import warnings
warnings.filterwarnings('ignore')
import seaborn as sns
import matplotlib.pylab as plt
import numpy as np
from scipy import stats
import sys
import os
sys.path.append(os.path.dirname(os.path.abspath(os.path.dirname('github'))))
import utils.statsmodel_helper as sh
import utils.feature_selection as fs
import utils.preprocessing as pp
import utils.error_calculator as ec
import utils.helpermodeling as hm
from scipy import stats

from sklearn.model_selection import train_test_split, ShuffleSplit
from sklearn.model_selection import KFold, ParameterGrid, cross_val_score, GridSearchCV

from sklearn.metrics import mean_squared_error, mean_absolute_error
from sklearn.metrics import r2_score, explained_variance_score

# model import
from sklearn.ensemble import RandomForestRegressor
from sklearn.tree import DecisionTreeRegressor
from sklearn.svm import SVR
import xgboost as xgb

from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.pipeline import Pipeline

cv = KFold(n_splits=5, shuffle=True, random_state=1)

In [2]:
df_train = pd.read_csv('../input/train_macro_without_outliers.csv', index_col=0)
df_train_augmented = pd.read_csv('../input/train_macro_with_outliers.csv', index_col=0)
df_test = pd.read_csv('../input/test_macro.csv', index_col=0)

In [ ]:
df_train.tail(2)

In [ ]:
df_train_augmented.tail(2)

In [ ]:
df_test.tail(2)

## 1. Preprocessing

In [3]:
onem = df_train_augmented[df_train_augmented.price_doc == 1000000]
twom = df_train_augmented[df_train_augmented.price_doc == 2000000]
print(df_train.shape, onem.shape, twom.shape)
df_train_augmented = df_train.append(onem, ignore_index=True)
df_train_augmented = df_train_augmented.append(twom, ignore_index=True)
print(df_train.shape, df_train_augmented.shape, onem.shape, twom.shape)

(25037, 151) (744, 151) (756, 151)
(25037, 151) (26537, 151) (744, 151) (756, 151)


In [4]:
cate_features = [
 'detention_facility_raion',
 'culture_objects_top_25',
 'railroad_1line',
 'big_market_raion',
 'incineration_raion',
 'big_road1_1line',
 'radiation_raion',
 'railroad_terminal_raion',
 'ecology',
 'thermal_power_plant_raion',
 'oil_chemistry_raion',
 'nuclear_reactor_raion',
 'product_type',
 'water_1line'
]

numeric_features = list(df_train.columns.drop(cate_features + ['price_doc']).values)

### Lable-Encoding

In [5]:
for f in cate_features:
    df_train[f].fillna(df_train[f].value_counts().index[0], inplace=True)
    df_test[f].fillna(df_test[f].value_counts().index[0], inplace=True)
    df_train_augmented[f].fillna(df_train_augmented[f].value_counts().index[0], inplace=True)
    
    lbl = LabelEncoder()
    lbl.fit(df_train[f].values)
    df_train[f] = lbl.transform(df_train[f].values)
    df_test[f] = lbl.transform(df_test[f].values)
    df_train_augmented[f] = LabelEncoder().fit_transform(df_train_augmented[f].values)

### Log nomalizaion

In [6]:
# Log Normalization of Numeric Features
numeric_features = list(df_train.columns.drop(cate_features + ['price_doc']).values)

for column in numeric_features + ['price_doc']:
    if stats.skew(df_train[column].values) > 1:
        df_train[column] = np.log(df_train[column] + 1)  
        df_train_augmented[column] = np.log(df_train_augmented[column] + 1)
        if column in df_test.columns.values:
            df_test[column]  = np.log(df_test[column] + 1)

### Standard scaling

In [7]:
# 평균 0 표준편차 1이 되도록 스케일링
train_scaler = StandardScaler()
train_scaler.fit(df_train[numeric_features])

scaled_numeric_train_X = train_scaler.transform(df_train[numeric_features])
df_scaled_numeric_train_X = pd.DataFrame(scaled_numeric_train_X, index=df_train.index, columns=numeric_features)
df_train = pd.concat([df_scaled_numeric_train_X, df_train[cate_features], df_train['price_doc']], axis=1)

scaled_numeric_test_X = train_scaler.transform(df_test[numeric_features])
df_scaled_numeric_test_X = pd.DataFrame(scaled_numeric_test_X, index=df_test.index, columns=numeric_features)
df_test = pd.concat([df_scaled_numeric_test_X, df_train[cate_features]], axis=1)

scaled_numeric_train_X = train_scaler.transform(df_train_augmented[numeric_features])
df_scaled_numeric_train_X = pd.DataFrame(scaled_numeric_train_X, index=df_train_augmented.index, columns=numeric_features)
df_train_augmented = pd.concat([df_scaled_numeric_train_X, df_train_augmented[cate_features], df_train_augmented['price_doc']],axis=1)

# 2. Regressors : Scikit-Learn
- Decision Tree Regressor
- RandomForest Regressor
- Support Vector Regressor
- XGB(Extreme Gradient Boosting) Regressor
- Cross-validation

In [8]:
X_train, X_test, y_train, y_test = train_test_split(df_train[numeric_features+cate_features], df_train['price_doc'], test_size=0.2, random_state=1)

### Decision Tree Regressor

In [ ]:
dtr = DecisionTreeRegressor()
y_train_dtr, y_test_dtr = hm.regression(dtr, X_train, X_test, y_train)
hm.scores('Decision Tree Regressor', y_train, y_test, y_train_dtr, y_test_dtr)

### cross validation

In [ ]:
cross_val_score(dtr, X_train, y_train, scoring='r2', cv=cv)

In [ ]:
cross_val_score(dtr, X_train, y_train, scoring='neg_mean_squared_log_error', cv=cv)

## RandomForest Regressor

In [ ]:
rfr = RandomForestRegressor()
y_train_rfr, y_test_rfr = hm.regression(rfr, X_train, X_test, y_train)
hm.scores('RandomForest Regressor', y_train, y_test, y_train_rfr, y_test_rfr)

### cross validation

In [ ]:
cross_val_score(rfr, X_train, y_train, scoring='r2', cv=cv)

In [ ]:
cross_val_score(rfr, X_train, y_train, scoring='neg_mean_squared_log_error', cv=cv)

## Support Vector Regressor

In [ ]:
svr = SVR(gamma='scale', C=1.0, epsilon=0.2)
y_train_rfr, y_test_rfr = hm.regression(svr, X_train, X_test, y_train)
hm.scores('Support Vector Regressor', y_train, y_test, y_train_rfr, y_test_rfr)

### cross validation

In [ ]:
cross_val_score(svr, X_train, y_train, scoring='r2', cv=cv)

In [ ]:
cross_val_score(svr, X_train, y_train, scoring='neg_mean_squared_log_error', cv=cv)

## XGB Regressor

In [10]:
param_grid = [{
    'max_depth': [10],
    'learning_rate' : [0.1],
    'n_estimators' : [200], 
    'colsample_bytree': [0.5]
}]

xgr = xgb.XGBRegressor()
grid_xgr = GridSearchCV(xgr, param_grid, cv=cv, n_jobs=4, scoring='neg_mean_squared_log_error')
grid_xgr.fit(X_train, y_train)
print(grid_xgr.best_estimator_)

XGBRegressor(base_score=0.5, booster='gbtree', colsample_bylevel=1,
       colsample_bytree=0.5, gamma=0, learning_rate=0.1, max_delta_step=0,
       max_depth=10, min_child_weight=1, missing=None, n_estimators=200,
       n_jobs=1, nthread=None, objective='reg:linear', random_state=0,
       reg_alpha=0, reg_lambda=1, scale_pos_weight=1, seed=None,
       silent=True, subsample=1)


In [11]:
xgr = xgb.XGBRegressor(base_score=0.5, booster='gbtree', colsample_bylevel=1,
       colsample_bytree=0.5, gamma=0, learning_rate=0.1, max_delta_step=0,
       max_depth=10, min_child_weight=1, missing=None, n_estimators=200,
       n_jobs=1, nthread=None, objective='reg:linear', random_state=0,
       reg_alpha=0, reg_lambda=1, scale_pos_weight=1, seed=None,
       silent=True, subsample=1)
# y_train_xgr, y_test_xgr = hm.regression(xgr, X_train, X_test, y_train)
# hm.scores('XGB Regressor', y_train, y_test, y_train_xgr, y_test_xgr)

In [ ]:
cross_val_score(xgr, X_train, y_train, scoring='r2', cv=cv)

In [ ]:
cross_val_score(xgr, X_train, y_train, scoring='neg_mean_squared_log_error', cv=cv)

In [ ]:
prediction = grid_xgr.best_estimator_.predict(X_test)
sns.distplot(prediction)

### Cross Validation

In [ ]:
def show_results(y_test, pred, measured, preds):
    print('\n')
    print("Train Test Split")
    print('RMSE:', np.sqrt(mean_squared_error(y_test, pred)))

    print('\n')
    print("Cross Validation")
    print('RMSE:', np.sqrt(mean_squared_error(measured, preds)))

    fig  = plt.figure(figsize=(8, 4), dpi=100)
    axes1 = fig.add_subplot(121)
    axes1.scatter(y_test, pred, c='red', s=5)
    axes1.plot([y_test.min(), y_test.max()], [y_test.min(), y_test.max()], 'k--', lw=2)
    axes1.set_title("Train Test Split")
    axes1.set_xlabel('Measured')
    axes1.set_ylabel('Predicted')
    axes2 = fig.add_subplot(122)
    axes2.scatter(measured, preds, c='red', s=5)
    axes2.plot([y_test.min(), y_test.max()], [y_test.min(), y_test.max()], 'k--', lw=2)
    axes2.set_title("Cross Validation")
    axes2.set_xlabel('Measured')
    axes2.set_ylabel('Predicted')
    fig.tight_layout()
    
    fig  = plt.figure(figsize=(8, 4), dpi=100);
    axes1 = fig.add_subplot(121); 
    axes1.scatter(y_test, y_test-pred, c='red', s=2)
    axes1.set_title("Train Test Split")
    axes1.set_xlabel('Measured')
    axes1.set_ylabel('Residual')
    axes2 = fig.add_subplot(122); 
    axes2.scatter(measured, measured-preds, c='red', s=2)
    axes2.set_title("Cross Validation")
    axes2.set_xlabel('Measured')
    axes2.set_ylabel('Residual')
    fig.tight_layout();
    
    fig  = plt.figure(figsize=(8, 4), dpi=100)
    axes1 = fig.add_subplot(121)
    axes2 = fig.add_subplot(122)
    sns.distplot((y_test-pred), bins=50, ax=axes1, axlabel='Error Deviation', kde_kws={"color": "k", "lw": 1.5, "gridsize":1000}, hist_kws={"linewidth": 3, "alpha": 0.6, "color": "red"})
    sns.distplot((measured-preds), bins=50, ax=axes2, axlabel='Error Deviation', kde_kws={"color": "k", "lw": 1.5, "gridsize":1000}, hist_kws={"linewidth": 3, "alpha": 0.6, "color": "red"})
    axes1.set_title("Train Test Split")
    axes2.set_title("Cross Validation")
    axes1.set_xlim(-3, 3)
    axes2.set_xlim(-3, 3)
    

In [ ]:
predictions = cross_val_score(grid_xgr.best_estimator_, df_train[numeric_features+cate_features],
                             df_train['price_doc'], cv=cv)

show_results(y_test, prediction, df_train['price_doc'], predictions)

In [12]:
def calc_train_error(X_train, y_train, model):
    prediction = model.predict(X_train)
    mse = mean_squared_error(y_train, prediction)
    rmse = np.sqrt(mse)
    return rmse

def calc_validation_error(X_test, y_test, model):
    predictions = model.predict(X_test)
    mse = mean_squared_error(X_test, predictions)
    rmse = np.sqrt(mse)
    return rmse

def calc_matrix(X_train, y_train, X_test, y_test, model):
    model.fit(X_train, y_train)
    train_error =  calc_train_error(X_train, y_train, model)
    validation_error = calc_validation_error(X_test, y_test, model)
    return train_error, validation_error

In [13]:
# xgr
train_error, test_error = calc_matrix(X_train, y_train, X_test, y_test, xgr)

ValueError: y_true and y_pred have different number of output (150!=1)

In [16]:
len(xgr.predict(X_test))

5008

In [15]:
mean_squared_error(X_test, xgr.predict(X_test))

ValueError: y_true and y_pred have different number of output (150!=1)

In [17]:
X_test

usdrub   full_sq   life_sq     floor  num_room  kitch_sq     state  \
id                                                                            
15909 -0.074862 -0.750968 -0.355330 -0.904622  0.179317  0.115441 -0.302067   
30325  1.730123  0.655939  0.498255  0.244024  0.179317 -1.465379 -1.520629   
4711  -0.714394 -1.164538  0.199623 -1.096062 -0.736745 -0.053300 -0.579316   
14674 -0.311865 -0.909833 -0.844628 -0.330299 -1.166240  0.535829  1.452309   
4391  -0.772889 -1.346777 -0.753680 -0.904622 -0.814332  0.445350  0.324704   
12835 -0.541291 -0.829382 -0.844628  1.392669 -1.166240  0.535829  1.452309   
7300  -0.761332 -1.442083 -0.666945  0.244024 -0.853126  0.602678  0.620440   
19703 -0.291822  0.556021  0.669188 -1.096062  1.524874  0.340487 -0.034160   
30268  1.775381  1.583593  1.858540  1.201228  1.524874 -1.465379 -1.520629   
12860 -0.575082 -1.164538 -0.844628  0.244024 -1.166240  0.862965  1.452309   
10593 -0.638406 -0.674491 -0.304538  0.244024 -1.166240 -1.465379 -0.067544   
17872 -0.133731  1.236964  1.649161 -1.096062  0.179317 -1.465379 -1.520629   
14244 -0.289221 -0.122425  0.028486  0.626905 -1.166240 -2.423975 -0.575964   
3989  -0.806412  0.504827  0.407035 -1.096062  0.233092 -0.082436 -0.616681   
12626 -0.520001  0.235338  0.303425 -0.713181  1.524874  0.115441 -0.034160   
23799  0.447794  0.452773  0.145481  1.392669  0.179317  1.002923 -0.599031   
24351  1.047725  0.235338  0.145481 -1.287503  0.179317  0.535829  1.452309   
29388  1.451695  0.291144 -0.027017 -0.521740  0.179317  1.248518  1.452309   
27949  2.413040 -0.386174 -0.130635  0.818346 -1.166240 -1.465379 -1.520629   
18544 -0.299911 -1.641970 -1.260283  0.435465 -1.166240  0.340487  1.452309   
8395  -0.654204  0.504827  0.627187 -0.713181  0.233092  0.609258  0.811006   
16461 -0.189846 -0.318101 -0.088237  0.052583  0.179317  0.535829  0.011654   
8375  -0.654204 -0.750968 -0.844628 -1.287503 -0.542778  0.670829  0.732590   
25093  0.970672 -1.442083 -1.260283 -0.330299 -1.166240  0.862965 -0.034160   
9901  -0.546740  0.752733  1.356717  0.435465  0.427059 -0.001478 -0.511009   
17358 -0.148953 -1.077288 -0.753680  0.818346 -1.166240  0.862965 -0.034160   
15927 -0.074862  1.069509  0.975065 -0.904622  1.524874  0.708403  1.452309   
10541 -0.639155 -0.829382 -0.753680 -0.904622 -1.166240  0.708403  0.274604   
28560  2.039483  0.556021  0.437938 -0.904622  0.179317 -1.465379 -1.520629   
2664  -0.542330 -0.992429 -0.844628 -1.096062 -0.659158  0.314445  0.137767   
15106 -0.235303 -0.599857 -0.940218  1.392669 -1.166240 -1.465379 -1.520629   
20464 -0.402537 -1.077288 -1.147408 -1.096062 -1.166240  0.862965  1.452309   
6482  -0.862197  1.395829  0.945006  1.775551  1.008962 -0.015264 -0.575964   
3708  -0.795489  0.235338  0.089728  0.435465  0.039125  0.647060  0.363632   
10973 -0.650870 -0.674491 -0.940218 -0.904622 -1.166240 -1.465379 -0.677001   
5188  -0.861173 -0.059854  0.066241 -0.904622 -0.154843 -0.082436 -0.616681   
10774 -0.632511 -0.455776 -0.151525 -0.904622  0.179317  0.340487  1.452309   
11765 -0.620405  0.235338 -0.027017 -0.521740  0.179317  0.708403 -0.034160   
8009  -0.784606  0.452773  0.375614  0.818346  0.194298 -0.099002 -0.637569   
17060 -0.184860 -0.992429 -0.844628 -1.096062 -1.166240  0.708403 -0.034160   
13458 -0.583771 -0.829382 -0.397945 -0.138858 -1.166240 -1.465379 -1.520629   
2973  -0.539282 -1.641970 -0.217027 -0.521740 -0.930713  0.101085 -0.286540   
13205 -0.554612 -0.750968 -0.504665  0.435465  0.179317  0.340487  0.248186   
24736  1.116753  0.752733  0.556690 -0.521740  0.179317 -1.465379 -1.520629   
14928 -0.289904 -0.674491 -0.304538  0.435465 -1.166240 -1.465379 -0.664490   
540   -0.768540 -1.346777 -0.940218  0.244024 -0.814332  0.499858  0.604410   
5916  -0.977385  1.195942  0.710268 -0.138858  0.814994  0.492298  0.708183   
23849  0.496547 -0.674491 -0.304538 -0.330299 -1.166240 -1.465379 -0.664490   
8462  -0.618391  2.465472  1.468413  1.392669  2.289147  0.